In [1]:
# Importing pre-requisite libraries for the project

import requests
from urllib.parse import urlparse
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
import pandas as pd
import re
from itertools import cycle
import traceback
import smtplib
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText
from email.mime.application import MIMEApplication
import os
from dotenv import load_dotenv


# Setting up environment variables

load_dotenv()

True

In [2]:
# Initiate Selenium Framework (Chromium Headless Browser)

def initialize_chromium():
    options = webdriver.ChromeOptions()
    options.add_argument("--disable-infobars")
    options.add_argument("--start-maximized")
    options.add_argument("--disable-extensions")
    # options.add_argument('--window-size=764,1080')
    options.add_argument('--window-size=1920,1080')
    # options.add_argument("--headless")
    global driver; driver = webdriver.Chrome(options = options)


# Release Selenium Framework (Chromium Headless Browser)

def release_chromium():
    driver.close()

In [47]:
# Extracting the Regular Meetings data to a DataFrame

def meetings_extraction():
  # url = 'https://ottawapoliceboard.ca/opsb-cspo/meetings.html'
  # url = 'https://pub-ottawa.escribemeetings.com/?Expanded=Ottawa%20Police%20Services%20Board&Year=2023'
  # url = 'https://pub-ottawa.escribemeetings.com/Meeting.aspx?Id=3760766e-baa1-4574-a3c3-da5e7879c8c6&Agenda=Agenda&lang=English'

  global current_year; current_year = 2022
  meeting_no = 1
  reg_meets_all = []
  reg_meets = []
  reg_meets_cancelled = []
  reg_meets_without_verbals = []

  while current_year > 2010:
    url = f'https://ottawapoliceboard.ca/opsb-cspo/{current_year}-meetings.html'

    driver.get(url)
    page_src = driver.page_source
    soup = BeautifulSoup(page_src, 'html.parser')

    meetings_list = soup.find('table').find('tbody').find_all('tr')

    for index, tr in enumerate(reversed(meetings_list)):
        td = tr.find_all('td')
        if td[3].get_text().strip() == 'Regular Meeting':
          if current_year < 2013: date = f'{td[0].get_text().strip()}, {current_year}'
          else: date = td[0].get_text().strip()

          # driver.get(td[0].find('a').get('href'))
          # page_src = driver.page_source

          reg_meets_all.append({
              'Meeting #': meeting_no,
              'Date': date,
              'Location': td[1].get_text().strip(),
              'Time': td[2].get_text().strip(),
              'Meeting Type': td[3].get_text().strip(),
              'Meeting Page': td[0].find('a').get('href'),
              'Chief Verbal Report Present': '',
              'Verbal Report File URL': ''
            })
          meeting_no = meeting_no + 1
    print(f'Regular Meetings of Year {current_year} processed.')
    current_year = current_year - 1
  reg_meets_all_df = pd.DataFrame(reg_meets_all)

# Remove Cancelled Regular Meetings
# soup.find(lambda tag: tag.name == 'div' and 'I CAN NOT GET THIS' in tag.get_text())
  for x in reg_meets_all:
    if x['Location'] == 'CANCELLED':
      reg_meets_cancelled.append(x)
    else:
      reg_meets.append(x)
  reg_meets_cancelled_df = pd.DataFrame(reg_meets_cancelled)
  # reg_meets_df = pd.DataFrame(reg_meets)

  for meet in reg_meets:
    # initialize_chromium()
    reports = []

    url = meet['Meeting Page']
    domain = '{uri.scheme}://{uri.netloc}/'.format(uri = urlparse(url))
    driver.get(url)
    page_src = driver.page_source
    soup = BeautifulSoup(page_src, 'html.parser')


    if soup.find_all('div', text = lambda t: t and any(x in t for x in ["Chief’s report", "Chief's report"])):
      elems = soup.find_all('div', text = lambda t: t and any(x in t for x in ["Chief’s report", "Chief's report"]))
      for el in elems:
        for a in el.find_parent().find_all('a', href = lambda href: href and "filestream" in href):
            # if "filestream" in a['href']:
              reports.append(domain + a['href'])
              meet.update({'Chief Verbal Report Present': 'Yes'})
              meet.update({'Verbal Report File URL': reports})
            # else:
            #   meet.update({'Chief Verbal Report Present': 'No'})
            #   meet.update({'Verbal Report File URL': '-'})
    elif soup.find_all(text = lambda t: t and any(x in t for x in ["Chief’s report", "Chief's report"])):
      elems = soup.find_all(text = lambda t: t and any(x in t for x in ["Chief’s report", "Chief's report"]))
      for el in elems:
          # for a in el.find_parent().find_all('a', href = True):
          for a in ((((el.find_parent()).find_parent()).find_parent()).find_parent()).find_parent().find_all('a', href = lambda href: href and "filestream" in href):
              # if "filestream" in a['href']:
                reports.append(domain + a['href'])
                meet.update({'Chief Verbal Report Present': 'Yes'})
                meet.update({'Verbal Report File URL': reports})


  reg_meets_df = pd.DataFrame(reg_meets)
  export_to_excel(reg_meets_df)


# # Check for Police Chief Verbals from the meetings list
#   for x in reg_meets:
#     url = f"{x['Meeting Page']}"
#     driver.get(url)
#     page_src = driver.page_source
#     soup = BeautifulSoup(page_src, 'html.parser')

    # chief_verbal_attachment = soup.find('table').find('tbody').find_all('tr')

# Export the DataFrame to an Excel Sheet

def export_to_excel(df):
  df.to_excel('regular_meetings_v2.0.xlsx', sheet_name = 'Regular Meetings')

In [44]:
initialize_chromium()

reports = []

# url = f"https://pub-ottawa.escribemeetings.com/Meeting.aspx?Id=791a957c-85f4-44b8-86a2-ce2ca3ea42c1&Agenda=Agenda&lang=English"
url = f"https://pub-ottawa.escribemeetings.com/Meeting.aspx?Id=66072621-496b-4c1b-bf2d-c9c6cfc8175d&Agenda=Agenda&lang=English"
domain = '{uri.scheme}://{uri.netloc}/'.format(uri = urlparse(url))
driver.get(url)
# driver.find_elements(by = "xpath", value = '''//*[text() = "Chief's report"]''')
page_src = driver.page_source
soup = BeautifulSoup(page_src, 'html.parser')

# for a in soup.find_all('div', text = re.compile("Chief's report"))
# elems = soup.find_all('div', text = re.compile("Chief’s report"))
elems = soup.find_all(text = lambda t: t and any(x in t for x in ["Chief’s report", "Chief's report"]))
for el in elems:
    # for a in el.find_parent().find_all('a', href = True):
    # print(((((el.find_parent()).find_parent()).find_parent()).find_parent()).find_parent())
    for a in el.find_parent().find_all('a', href = lambda href: href and "filestream" in href):
        # if "filestream" in a['href']:
            reports.append(domain + a['href'])
print(reports)
    # for a in ((el.find_parent()).find_parent()).find_parent().find_all('a', href = True):
    #     print ('here')
    #     if "filestream" in a['href']:
    #         print(a['href'])
# for x in driver.find_elements(by = "xpath", value = '''//*[text() = "Chief's report"]'''):
#     soup = BeautifulSoup(x.parent.page_source, 'html.parser')
#     print(soup)
# driver.find_element(by = "xpath", value = '''//*[contains(text(), "Chief's verbal report")]''').click()

# page_src = driver.page_source
# soup = BeautifulSoup(page_src, 'html.parser')

<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief's report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="AgendaItemContentRow indent"><div class="AgendaItemDescription RichText"><div><div><p>Chief’s report</p></div></div></div></div>
<div class="A

In [46]:
def send_mail():
    recipient_mail = input("Enter an E-mail address to receive missing chief's verbal list")
    to_mail = recipient_mail
    gmail_usr = os.getenv('GMAIL_USR')
    gmail_pwd = os.getenv('GMAIL_PWD')

    msg = MIMEMultipart()
    msg['Subject'] = "Missing Chief's Verbals List"
    msg['From'] = gmail_usr
    msg['To'] = to_mail

    msgText = MIMEText("\n This mail consists of regular meetings list where Chief's Verbal document is missing \n p.f.a. \n", 'html')
    msg.attach(msgText)

    filename = "regular_meetings_v2.0.xlsx"
    xlsx = MIMEApplication(open(filename, 'rb').read())
    xlsx.add_header('Content-Disposition', 'attachment', filename = 'missing_chief_verbals.xlsx')
    msg.attach(xlsx)

    # with open(filename, 'rb') as f:
    #     file_data = f.read()
    # smtpserver.add_attachment(file_data, maintype="application", subtype="xlsx", filename='regular_meetings.xlsx')

    try:
        with smtplib.SMTP("smtp.gmail.com", 587) as smtpserver:
            smtpserver.ehlo()
            smtpserver.starttls()
            smtpserver.login(gmail_usr, gmail_pwd)
            smtpserver.sendmail(f'{gmail_usr}<Team-8 SMTP Mail Client>', to_mail, msg.as_string())
            smtpserver.quit()
    except Exception as e:
        print(e)

    print ('email sent!')

In [49]:
initialize_chromium()
meetings_extraction()
release_chromium()
# send_mail()

Regular Meetings of Year 2022 processed.
Regular Meetings of Year 2021 processed.
Regular Meetings of Year 2020 processed.
Regular Meetings of Year 2019 processed.
Regular Meetings of Year 2018 processed.
Regular Meetings of Year 2017 processed.
Regular Meetings of Year 2016 processed.
Regular Meetings of Year 2015 processed.
Regular Meetings of Year 2014 processed.
Regular Meetings of Year 2013 processed.
Regular Meetings of Year 2012 processed.
Regular Meetings of Year 2011 processed.
<tbody><tr style="height:14.0pt">
<td style="width:36.0pt;padding:0cm 5.4pt 0cm 5.4pt;
  height:14.0pt" valign="top" width="48">
<h5 style="margin-top:6.0pt;margin-right:0cm;margin-bottom:6.0pt;margin-left:
  0cm;line-height:125%"><span lang="EN-US" style='font-size:12.0pt;line-height:
  125%;font-family:"Arial","sans-serif";font-weight:normal;font-style:normal'>2.</span></h5>
</td>
<td colspan="2" style="width:443.4pt;padding:0cm 5.4pt 0cm 5.4pt;
  height:14.0pt" valign="top" width="591">
<h5 style="ma